In [1]:
from PW_explorer.run_clingo import run_clingo
from PW_explorer.load_worlds import load_worlds
from PW_explorer.pwe_helper import rel_slicer
from PW_explorer.time_series import PWETimeSeriesModule
from PW_explorer.pwe_nb_helper import ASPRules
from PW_explorer.export import PWEExport
from PW_explorer.visualize import PWEVisualization

import pandas as pd

import networkx as nx
import matplotlib.pyplot as plt
from nxpd import draw
from nxpd import nxpdParams
nxpdParams['show'] = 'ipynb'
from copy import deepcopy
from collections import OrderedDict
import random
import csv
import numpy as np
import time

In [2]:
%load_ext PWE_NB_Extension

In [3]:
def turn_list_into_str(l):
    # small bug fix 
    if isinstance(l, (list,set,frozenset)):
        if len(l) > 1:
            l_ = [turn_list_into_str(l1) for l1 in l[1:]]
            return "{}({})".format(l[0], ",".join(l_))
        elif len(l) == 1:
            return "{}".format(l[0])
        else:
            return ""
    else:
        return l


In [118]:
def sql2clingo(sqlCommand,originalSchema,colour='black'):
    sql = sqlCommand.replace('"','')
    sqlList = sql.split(' ') 
    #print(sqlList)
    schemaList = originalSchema.split(',')
    #print(schemaList)
    clingoString = 0
    #print(sqlList[0])
    if sqlList[0] == 'UPDATE':
        sql = sql.replace(' = ','=')
        sql = sql.replace(' > ','>')
        sql = sql.replace(' < ','<')
        sql = sql.replace(' >= ','>=')
        sql = sql.replace(' <= ','<=')
        sql = sql.replace(',','')
        sqlList = sql.split(' ') 
        setLoc = sqlList.index('SET')
        whereLoc = sqlList.index('WHERE')
        setCommands = sqlList[setLoc+1:whereLoc]
        setCommands = [x.upper() for x in setCommands]
        whereCommands = sqlList[whereLoc+1:]
        whereCommands = [x.upper() for x in whereCommands if x != 'AND']
        whereCommandsString = '-'.join(whereCommands)
        whereCommandsComma = ','.join(whereCommands)
        setLocs = [x[:x.index('=')] for x in setCommands]
        setValues = [x[x.index('=')+1:] for x in setCommands]
        setVals = []
        startSetVals = []
        for x in (schemaList):
            if x in setLocs:
                loc = setLocs.index(x)
                setVals.append(setValues[loc])
                startSetVals.append('_')
            else:
                setVals.append(x)
                startSetVals.append(x)
        setValsString = ','.join(setVals)
        #clingoString = 'data('+setValsString+',black,"'+whereCommandsString+'",'+originalSchema+') :- data('+originalSchema+',_,_,_,_,_,_,_,_,_),'+whereCommandsComma+'.'
        clingoString = 'e(data('+setValsString+'),data1('+originalSchema+',P,N0),trans('+colour+',"'+whereCommandsString+'")) :- data1('+originalSchema+',P,N0),'+whereCommandsComma+'.'
    if sqlList[0] == 'INSERT':
        locator = 'VALUES('
        loc1 = sql.index(locator)
        loc2 = sql[loc1:].index(')')+loc1
        datavalues = sql[loc1+len(locator):loc2]
        datavaluesDash = datavalues.replace(',','-')
        clingoString = 'data1('+datavalues+',"INSERT'+datavaluesDash+'",0).'
    
    return clingoString

In [95]:
def makeOriginal(dataValues,colour='black'):
    clingoStart = []
    for x in dataValues:
        clingoStart.append('data1('+','.join(x)+',"",0).')
    return clingoStart

In [115]:
def addConversion(dataValues):
    variables = []
    #spaces = ['_']*len(dataValues)
    #underscores = ','.join(spaces)
        
    variables = [chr(65+x) for x in range(len(dataValues))]
    varLen = len(variables)
    variables2 = [chr(65+x+varLen) for x in range(len(dataValues))]
    clingoHead = 'data1('+','.join(variables)+',prov(P,T),N1) :- '
    clingoBody = 'e(data('+','.join(variables)+'),data1('+','.join(variables2)+',P,N0),trans(_,T)), N1=N0+1, depth(N0).'
    
    return clingoHead+clingoBody

In [97]:
def newAddConversion(dataValues):
    variables = [chr(65+x) for x in range(len(dataValues))]
    clingoHead = 'data('+','.join(variables)+') :- '
    clingoBody = 'data1('+','.join(variables)+',_,_).'
    return clingoHead+clingoBody

In [98]:
def addDepth(depthSize):
    depth = 'depth(0..{}).'.format(depthSize)
    return depth

In [99]:
def smallConvert(string):
    b = string.replace('data(','')
    b = b[:-1]
    c = b.replace('),',')\n')
    return c

In [100]:
def cleanCSVFile(csv,outCSV):
    with open(csv,'r') as f:
        data = f.read()
    dataNew = data.replace('(','')
    dataNew2 = dataNew.replace(')','')
    with open(outCSV,'w') as f:
        f.write(dataNew2)
    print(dataNew2)

In [188]:
def createProv(dataendRow,lenOriginalSchema=7):
    #print(dataendRow)
    string = dataendRow
    loc = 0
    for x in range(lenOriginalSchema):
        loc = string.find(',')+1
        string = string[loc:]
        
    #newString = string
    loc2 = string.rfind(',')
    string = string[:loc2]
    return string

In [189]:
createProv('data1(10,82,61,46,75,28,53,prov(prov("INSERT10-82-4-4-63-28-53","A4>=19-A4<29-A2>=2-A2<10"),"A1>=2-A1<12-A4>=20-A4<30"),2)')

'prov(prov("INSERT10-82-4-4-63-28-53","A4>=19-A4<29-A2>=2-A2<10"),"A1>=2-A1<12-A4>=20-A4<30")'

In [102]:
def getGraphStats(G,target,start):
    allPaths = []
    #for sources in dataValuesNonStr:
    singlePath = []
    for path in nx.all_simple_paths(G,source=start,target=target):
        singlePath.append(path)
    allPaths.append(singlePath)
    APP = len(allPaths[0])
    
    allPSorted = sorted(allPaths[0])
    allPSet = set(frozenset(x) for x in allPSorted)
    DIFF = [list(x) for x in allPSet]
    DIFFNUM = len(DIFF)
    
    minPath = nx.shortest_path(G,start,target)
    smallpp = len(minPath)
    #bigpp = nx.dag_longest_path_length(G)
    
    return [APP,DIFFNUM,smallpp]#,bigpp]

In [141]:
def createProvNew(startingProv,transCell):
    loc1 = transCell.index(',') +1
    loc2 = transCell.index(')')
    trans = transCell[loc1:loc2]
    
    prov = 'prov({},{})'.format(startingProv,trans)
    
    return prov

In [103]:
names = 'nodeNum,edgeNum,insertQueries,updateQueries,longPath,smallPath,medianPath'

In [104]:
originalSchema = 'id,a0,a1,a2,a3,a4,a5'.upper()

In [105]:
testDataNames = ['/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows10_Nqueries10.csv','/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows100_Nqueries10.csv','/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows1000_Nqueries10.csv']
testQueryNames = ['/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixQueries_Nrows10_Nqueries10.csv','/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixQueries_Nrows10_Nqueries20.csv','/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixQueries_Nrows10_Nqueries30.csv']

In [106]:
testDataNames = ['/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows10_Nqueries10.csv', '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows10_Nqueries20.csv', '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows10_Nqueries30.csv', '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows50_Nqueries10.csv', '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows50_Nqueries20.csv', '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows50_Nqueries30.csv', '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows100_Nqueries10.csv', '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows100_Nqueries20.csv', '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows100_Nqueries30.csv']
testQueryNames = ['/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixQueries_Nrows10_Nqueries10.csv','/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixQueries_Nrows10_Nqueries20.csv','/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixQueries_Nrows10_Nqueries30.csv']


In [107]:
testDataNames = ['/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows10_Nqueries10.csv','/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows50_Nqueries10.csv','/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows100_Nqueries10.csv']

In [108]:
testData = '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixData_Nrows50_Nqueries10S.csv'
testQueries = '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixQueries_Nrows50_Nqueries10.csv'

In [109]:
timings = []

In [277]:
testData = ''
testQueries = '/home/mj1e16/abduction/pwe/jupyterNotebooks/notInPWEenv/qfixQueries_Nrows10_Nqueries30Save.csv'
testData = testDataNames[1]

In [278]:
t0 =time.time()
# testData = testDataNames[0]
# testQueries = testQueryNames[2]
testDataOG = testData
cleanCSVFile(testData,'testData.csv')
testData = 'testData.csv'

0, 13, 85, 77, 27, 52, 48
1, 65, 79, 11, 5, 85, 46
2, 76, 1, 46, 73, 26, 95
3, 91, 4, 4, 56, 95, 41
4, 21, 43, 4, 24, 46, 52
5, 23, 24, 23, 48, 32, 7
6, 84, 56, 65, 21, 100, 87
7, 12, 34, 73, 72, 94, 45
8, 83, 68, 32, 60, 89, 86
9, 51, 59, 5, 26, 81, 44
10, 17, 55, 71, 69, 40, 47
11, 51, 78, 53, 41, 51, 7
12, 4, 71, 99, 61, 42, 21
13, 50, 99, 78, 55, 87, 27
14, 51, 96, 59, 47, 30, 57
15, 96, 1, 79, 83, 89, 76
16, 81, 52, 57, 44, 9, 88
17, 57, 20, 51, 50, 38, 38
18, 54, 63, 62, 47, 6, 27
19, 17, 59, 87, 81, 81, 83
20, 25, 85, 68, 11, 5, 6
21, 76, 25, 12, 64, 37, 11
22, 16, 53, 18, 29, 73, 48
23, 32, 48, 4, 40, 44, 23
24, 10, 90, 52, 23, 62, 83
25, 2, 2, 16, 73, 19, 72
26, 68, 55, 23, 98, 81, 54
27, 22, 65, 41, 59, 35, 65
28, 5, 30, 97, 88, 33, 87
29, 31, 94, 75, 43, 28, 5
30, 88, 4, 83, 97, 59, 21
31, 87, 98, 71, 52, 40, 38
32, 20, 68, 44, 22, 14, 68
33, 29, 50, 34, 88, 91, 6
34, 20, 33, 99, 79, 36, 25
35, 68, 84, 94, 36, 89, 70
36, 48, 99, 25, 74, 12, 21
37, 92, 22, 77, 61, 85, 40
38, 

In [279]:
dataSet = []
with open(testData,'r') as csvfile:
    reader = csv.reader(csvfile,delimiter=' ',quotechar='|')
    for row in reader:
        dataSet.append([' '.join(row)])

originalSetup = makeOriginal(dataSet)

with open(testQueries,'r') as f:
    data = f.read()
#print(data)    
queries = data.split('\n')
#print(queries)

commands = []
for x in queries:
    clingoString = sql2clingo(x,originalSchema)
    if clingoString != 0:
        commands.append(clingoString)
        
edgeNodeConv = addConversion(originalSchema.split(','))
nodeNodeConv = newAddConversion(originalSchema.split(','))
depth = addDepth(3)

clingo_rules = ['% schema data1('+originalSchema+',prov,NUM)','% schema e(DATAEND,DATASTART,TRANS)', '% schema data('+originalSchema+')']
clingo_rules.extend(originalSetup)
clingo_rules.extend([depth])
clingo_rules.extend([nodeNodeConv])
clingo_rules.extend(commands)
clingo_rules.extend([edgeNodeConv])



In [280]:
#ASPRules('\n'.join(commands))

In [281]:
#ASPRules('\n'.join(originalSetup))

In [282]:
#ASPRules(edgeNodeConv)

In [283]:
#ASPRules(nodeNodeConv)

In [284]:
#ASPRules('\n'.join(clingo_rules))

In [285]:
%clingo -l clingo_rules --saveto clingo_soln --save_meta_data_to meta_data --donot-display_input

Output:


'Answer: 1\ndepth(0) depth(1) depth(2) depth(3) data1(0,13,85,77,27,52,48,"",0) data1(1,65,79,11,5,85,46,"",0) data1(2,76,1,46,73,26,95,"",0) data1(3,91,4,4,56,95,41,"",0) data1(4,21,43,4,24,46,52,"",0) data1(5,23,24,23,48,32,7,"",0) data1(6,84,56,65,21,100,87,"",0) data1(7,12,34,73,72,94,45,"",0) data1(8,83,68,32,60,89,86,"",0) data1(9,51,59,5,26,81,44,"",0) data1(10,17,55,71,69,40,47,"",0) data1(11,51,78,53,41,51,7,"",0) data1(12,4,71,99,61,42,21,"",0) data1(13,50,99,78,55,87,27,"",0) data1(14,51,96,59,47,30,57,"",0) data1(15,96,1,79,83,89,76,"",0) data1(16,81,52,57,44,9,88,"",0) data1(17,57,20,51,50,38,38,"",0) data1(18,54,63,62,47,6,27,"",0) data1(19,17,59,87,81,81,83,"",0) data1(20,25,85,68,11,5,6,"",0) data1(21,76,25,12,64,37,11,"",0) data1(22,16,53,18,29,73,48,"",0) data1(23,32,48,4,40,44,23,"",0) data1(24,10,90,52,23,62,83,"",0) data1(25,2,2,16,73,19,72,"",0) data1(26,68,55,23,98,81,54,"",0) data1(27,22,65,41,59,35,65,"",0) data1(28,5,30,97,88,33,87,"",0) data1(29,31,94,75,43,28,5,"",0) data1(30,88,4,83,97,59,21,"",0) data1(31,87,98,71,52,40,38,"",0) data1(32,20,68,44,22,14,68,"",0) data1(33,29,50,34,88,91,6,"",0) data1(34,20,33,99,79,36,25,"",0) data1(35,68,84,94,36,89,70,"",0) data1(36,48,99,25,74,12,21,"",0) data1(37,92,22,77,61,85,40,"",0) data1(38,34,30,87,62,96,90,"",0) data1(39,13,56,12,6,11,88,"",0) data1(40,79,83,35,63,79,41,"",0) data1(41,57,23,10,29,90,59,"",0) data1(42,93,46,29,80,84,6,"",0) data1(43,67,10,13,89,7,28,"",0) data1(44,99,43,13,19,27,76,"",0) data1(45,10,92,39,98,92,33,"",0) data1(46,25,48,11,66,7,6,"",0) data1(47,99,30,61,47,34,11,"",0) data1(48,92,97,98,13,24,64,"",0) data1(49,98,55,70,67,29,56,"",0) data1(10,44,50,23,23,22,46,"INSERT10-44-50-23-23-22-46",0) data1(11,2,84,56,64,18,100,"INSERT11-2-84-56-64-18-100",0) data1(12,4,71,99,59,39,17,"INSERT12-4-71-99-59-39-17",0) data1(13,59,86,80,80,82,25,"INSERT13-59-86-80-80-82-25",0) data1(14,11,63,34,7,16,53,"INSERT14-11-63-34-7-16-53",0) data1(15,27,71,45,32,47,2,"INSERT15-27-71-45-32-47-2",0) data1(16,61,82,2,1,14,72,"INSERT16-61-82-2-1-14-72",0) data1(17,71,68,55,22,98,80,"INSERT17-71-68-55-22-98-80",0) data1(18,88,3,82,97,57,17,"INSERT18-88-3-82-97-57-17",0) data1(19,68,43,19,10,67,29,"INSERT19-68-43-19-10-67-29",0) data1(10,46,32,38,90,53,56,"INSERT10-46-32-38-90-53-56",0) data1(11,2,32,13,51,100,68,"INSERT11-2-32-13-51-100-68",0) data1(12,90,80,74,91,77,79,"INSERT12-90-80-74-91-77-79",0) data1(13,88,10,52,86,24,21,"INSERT13-88-10-52-86-24-21",0) data1(14,82,15,18,69,38,4,"INSERT14-82-15-18-69-38-4",0) data1(15,34,3,45,77,74,91,"INSERT15-34-3-45-77-74-91",0) data1(16,10,45,88,12,59,39,"INSERT16-10-45-88-12-59-39",0) data1(17,56,14,5,3,16,9,"INSERT17-56-14-5-3-16-9",0) data1(18,42,53,0,3,41,11,"INSERT18-42-53-0-3-41-11",0) data1(13,88,10,52,86,73,21,"INSERT13-88-10-52-86-73-21",0) data1(10,64,87,52,74,67,6,"INSERT10-64-87-52-74-67-6",0) data1(11,6,86,99,8,80,41,"INSERT11-6-86-99-8-80-41",0) data1(12,29,77,88,4,62,4,"INSERT12-29-77-88-4-62-4",0) data1(13,7,60,3,19,41,61,"INSERT13-7-60-3-19-41-61",0) data1(14,4,87,31,96,90,38,"INSERT14-4-87-31-96-90-38",0) data1(15,62,63,6,63,47,68,"INSERT15-62-63-6-63-47-68",0) data1(16,37,60,30,38,77,2,"INSERT16-37-60-30-38-77-2",0) data1(17,43,70,10,32,33,84,"INSERT17-43-70-10-32-33-84",0) data1(18,75,84,66,52,29,34,"INSERT18-75-84-66-52-29-34",0) data1(19,6,59,28,81,4,91,"INSERT19-6-59-28-81-4-91",0) data1(10,82,4,4,63,28,53,"INSERT10-82-4-4-63-28-53",0) data1(11,33,17,46,4,70,90,"INSERT11-33-17-46-4-70-90",0) data1(12,44,13,38,97,33,0,"INSERT12-44-13-38-97-33-0",0) data1(13,17,79,36,29,9,99,"INSERT13-17-79-36-29-9-99",0) data1(14,4,49,25,100,12,53,"INSERT14-4-49-25-100-12-53",0) data1(15,42,25,89,83,50,3,"INSERT15-42-25-89-83-50-3",0) data1(16,24,21,23,87,14,5,"INSERT16-24-21-23-87-14-5",0) data1(46,25,48,53,47,7,6,prov("","A4>=2-A4<12-A2>=3-A2<13"),1) data1(39,13,56,53,47,11,88,prov("","A4>=2-A4<12-A2>=3-A2<13"),1) data1(10,82,4,93,75,28,53,prov("INSERT10-82-4-4-63-28-53","A4>=19-A4<29-A2>=0-A2<10"),1) d

In [286]:
pw_rels_dfs, rel_schemas, pw_objs = load_worlds(asp_output=clingo_soln, meta_data=meta_data, reasoner='clingo',internal_facts_as_string=False)

Number of Models: 1


In [287]:
pw_rels_dfs.keys()

dict_keys(['depth_1', 'data1_9', 'data_7', 'e_3'])

In [288]:
pwe_e3_new_format = pw_rels_dfs['e_3'].applymap(turn_list_into_str)
pwe_data3_new_format = pw_rels_dfs['data1_9'].applymap(turn_list_into_str)

In [289]:
start_col_names = ['ID','A0','A1','A2','A3','A4','A5']

startNode = []
for i, row in pwe_data3_new_format.iterrows():
    #print(len(row['prov']))
    if len(row['prov']) == 2:
        startNode.append('('+"{}".format(','.join([row[col] for col in start_col_names]))+')')

G = nx.DiGraph()
#start = '\n'.join(startNode) # for full db
start = 'Initial DB' # for names only

edges = []
provlist = []
num = 0
# for inserts in insertNodeList:
#     endInsert = '\n'.join(inserts)
#     G.add_edge(start,endInsert,penwidth=2,color='red')
#     edges.append((start,endInsert)) # for full values

start_col_names = ['ID','A0','A1','A2','A3','A4','A5']

insertNodeList = []
insertNodeProv = []
nodeDict = {}
nodeNameDict = {}
insertNameDict = {}
nodeDict["start"] = [x for x in startNode]
nodeDict['""'] = [x for x in startNode]
nodeNameDict["start"] = 'Initial DB'
for i, row in pwe_data3_new_format.iterrows():
    #print(len(row['prov']))
    #insertBase = startNode
    if 'INSERT' in row['prov']:
        if 'prov' not in row['prov']: 
            insertNode = [x for x in startNode]
            insertNode.append('('+"{}".format(','.join([row[col] for col in start_col_names]))+')')
            #print(insertNode)
            insertNodeList.append(insertNode)
            insertNodeProv.append(row['prov'])
            nodeDict[row['prov']] = insertNode
            nodeNameDict[row['prov']] = 'insertView '+str(num)
            insertNameDict[row['prov']] = 'insertView '+str(num)
            num += 1
            #print(row['prov'])
#print(nodeDict)  
# for key,inserts in insertNameDict.items():
#     endInsert = inserts
#     G.add_edge(start,endInsert,penwidth=2,color='red')
#     edges.append((start,endInsert)) # for names only
    
for inserts in insertNodeList:
    #endInsert = inserts
    endInsert = '\n'.join(inserts)
    startInsertNodeNewName = '\n'.join(nodeDict['""'])
    G.add_edge(startInsertNodeNewName,endInsert,penwidth=2,color='red')
    edges.append((startInsertNodeNewName,endInsert)) # for names only 

for i, row in pw_rels_dfs['e_3'].iterrows():
    #print(startProv)
    startProv = createProv(pwe_e3_new_format['DATASTART'][i])
    #print(startProv)
    #endProv = 'prov({},{})'.format(startProv,)
    endProv = createProvNew(startProv,pwe_e3_new_format['TRANS'][i])
    #print(type(endProv))
    nodeBase = nodeDict[startProv]
    #print(nodeBase)
    ignoreRow = row['DATASTART'][1:-1]
    nodeBase = [x for x in nodeBase if x != ignoreRow]
    nodeBase.append(','.join(row['DATAEND'][1:-1]))
    nodeFinal = nodeBase
    #print(nodeFinal)
    nodeDict[endProv] = nodeFinal
    nodeNameDict[endProv] = 'Table{}'.format(i)
    #print(nodeFinal)
    finalNetworkXStartNode = '\n'.join(nodeDict[startProv])
    finalNetworkXEndNode = '\n'.join(nodeDict[endProv])
    G.add_edge(finalNetworkXStartNode,finalNetworkXEndNode ,penwidth=2,color='blue')
#     print(row['DATASTART'])
#     print(row['DATAEND'])

In [291]:
for node in G.nodes: G.nodes[node]['fontname'] = 'Helvetica'
#G.graph['layout'] = 'fdp'

draw(G,'bigG.png')

In [1301]:
start = nodeDict['start']
startNode = '\n'.join(start)
startNode = nodeNameDict['start']
startNode = '\n'.join(nodeDict['""'])

nodeKeys = list(nodeDict.keys())
targetNum = 10
targets = []
for x in range(targetNum):
    targets.append(random.randint(0,len(nodeDict)-1))

targetPos = [nodeDict[nodeKeys[x]] for x in targets]
targetPos = ['\n'.join(x) for x in targetPos]
#targetNewFormat = ['\n'.join(t) for t in targetPos]

In [1302]:
nodelist = list(nodeDict.keys())
nodeList = [nodeDict[x] for x in nodelist]
graphNodeList = ['\n'.join(x) for x in nodeList]

pathLength = []
statyBojangles = []
for x in graphNodeList:
    singleStats = getGraphStats(G,x,startNode)
    statyBojangles.append(singleStats)
    pathLength.append(singleStats[-1])
    
longPath = max(pathLength)
smallPath = min(pathLength)
medianPath = int(np.median(pathLength))
nodeNum = G.number_of_nodes()
edgeNum = G.number_of_edges()

insertQueries = 0
updateQueries = 0
for x in queries:
    if 'INSERT' in x:
        insertQueries += 1
    if 'UPDATE' in x:
        updateQueries +=1
        
print(insertQueries,updateQueries)

results = '{} & {} & {} & {} & {} & {} & {}'.format(nodeNum,edgeNum,insertQueries,updateQueries,longPath,smallPath,medianPath)

with open('resultsDump.txt','a') as f:
    f.write(names+'\n'+results+'\n'+testDataOG+'\n'+testQueries+'\n\n')

72 168


In [1303]:
timings.append(time.time()-t0)

In [1304]:
timings

[5.157607078552246,
 4.879022836685181,
 5.009679079055786,
 5.12174391746521,
 4.915562152862549]